## Imports

In [22]:
from premise import *
import bw2data as bd
import bw2io as bo
import numpy as np
import pandas as pd
import bw2calc as bc
#import brightway2 as bw


import os, csv, json, requests
import glob
import pycountry
import pandas as pd
import numpy as np
from datetime import date
import pickle


### Project set up

In [2]:
bd.projects.set_current("MPTEX")

In [3]:
bo.bw2setup()

Biosphere database already present!!! No setup is needed


In [4]:
bd.databases

Databases dictionary with 4 object(s):
	biosphere3
	ecoinvent 3.9.1 cutoff
	image-SSP2-RCP19-2020
	image-SSP2-RCP19-2025

In [5]:
# file path to the place with the ecoinvent spold files (datasets directory)
fpei39 = "/etc/data/ecospold/datasets"
if 'ecoinvent 3.9.1 cutoff' in bd.databases:
    print("Database has already been imported")
else:
    ei39 = bo.SingleOutputEcospold2Importer(fpei39, 'ecoinvent 3.9.1 cutoff')
    ei39.apply_strategies()
    ei39.statistics()
    
    if len(list(ei39.unlinked)) == 0:
        ei39.write_database()

Database has already been imported


In [6]:
ndb = NewDatabase(
    scenarios=[
        {"model":"image", "pathway":"SSP2-RCP19", "year":2025},
        #{"model":"image", "pathway":"SSP2-RCP19", "year":2030},
        #{"model":"image", "pathway":"SSP2-RCP19", "year":2050},
        #{"model":"remind","pathway":"SSP2-Base","year":2039}
    ],
    source_db="ecoinvent 3.9.1 cutoff", # <-- name of the database in the BW2 project. Must be a string.
    source_version="3.9", # <-- version of ecoinvent. Can be "3.5", "3.6", "3.7" or "3.8". Must be a string.
    key='tUePmX_S5B8ieZkkM7WUU2CnO8SmShwmAeWK9x2rTFo=' # <-- decryption key
    # to be requested from the library maintainers if you want ot use default scenarios included in `premise`
)

premise v.(2, 1, 0)
+------------------------------------------------------------------+
| Warning                                                          |
+------------------------------------------------------------------+
| Because some of the scenarios can yield LCI databases            |
| containing net negative emission technologies (NET),             |
| it is advised to account for biogenic CO2 flows when calculating |
| Global Warming potential indicators.                             |
| `premise_gwp` provides characterization factors for such flows.  |
| It also provides factors for hydrogen emissions to air.          |
|                                                                  |
| Within your bw2 project:                                         |
| from premise_gwp import add_premise_gwp                          |
| add_premise_gwp()                                                |
+------------------------------------------------------------------+
+-------------

In [7]:
ndb.update()

Processing scenarios: 100%|█████████████| 1/1 [01:23<00:00, 83.93s/it]

Done!



In [8]:
#Save as a database
ndb.write_db_to_brightway(name=["image-SSP2-RCP19-2025",])

Write new database(s) to Brightway.
Running all checks...
Minor anomalies found: check the change report.
Database image-SSP2-RCP19-2025 already exists: it will be overwritten.
Title: Writing activities to SQLite3 database:
  Started: 05/24/2024 15:00:12
  Finished: 05/24/2024 15:00:44
  Total time elapsed: 00:00:32
  CPU %: 100.00
  Memory %: 3.22
Created database: image-SSP2-RCP19-2025
Generate scenario report.
Report saved under /home/jupyter-xtdds_s2024/MPTEX/export/scenario_report.
Generate change report.
Report saved under /home/jupyter-xtdds_s2024/MPTEX.


## PV dataset look-up

In [6]:
def pv_market_mixes_identifier(db_name) :
    """
    Function to list and parse pv datasets affecting an energy grid mix.
    """
    market_group_ds_storage = []
    market_ds_storage = []
    storage = []

    market_group_ds = []
    market_ds = []

    # Strategy filtering : is the dataset part of a market group or a basic market electricity grid mix 
    for ds in bd.Database(db_name) : 
        if 'market for electricity' in ds['name'] :
            group_counter = 0
            for exc in ds.exchanges(): 
                if 'market group for electricity' in exc['name'] : 
                    group_counter +=1 
            if group_counter == 0 : 
                market_ds.append((ds['name'],ds['code'])) 
            else : 
                market_group_ds.append((ds['name'],ds['location'],exc['input']))

    # Find if there are pv technologies involved with any of the market datasets : 
    for market in market_ds : 
        ds = bd.get_activity((db_name,market[1]))
        for exc in ds.exchanges() :
            if 'photovoltaic' in exc.input['name'] :
                # Extract the dataset name
                dataset_name = exc.input['name'] 
                # Make the name usable
                parsed_name = pv_name_parser(dataset_name)
                if 'roof' in parsed_name[1] : 
                    parsed_name.append(' on roof')
                elif 'facade' in parsed_name[1] : 
                    parsed_name.append('at building')
                else :
                    parsed_name.append('on open ground')
                
                # skip non pv energy producing datasets 
                if not any('kWp' in s for s in parsed_name) : 
                    continue  
                # Clear the kWp unit from the name
                parsed_name = [sub.replace('kWp','') for sub in parsed_name]
                # Store the market datasets and relevant information :
                market_ds_storage.append((ds['name'],ds['location'],np.nan,exc.input['code'],*parsed_name))
                
    # Find if there are pv technologies involved with any of the market GROUP datasets : 
    for market_group in market_group_ds : 
        group_ds = bd.get_activity((market_group[2]))
        # Note : the market groups typically have an intermediate dataset splitting commercial/residential
        for exc in group_ds.exchanges(): 
            if 'photovoltaic' in exc.input['name']: 
                production_sector = bd.get_activity((db_name,exc.input['code']))

                # Find the specific pv dataset technology & unit quantity
                for exc2 in production_sector.exchanges():
                    if 'photovoltaic' in exc2['name'] :
                        #print(exc2['name'],exc2['location'],exc2['unit'], exc['type'],exc2['amount'])
                        
                        # Extract the dataset name
                        parsed_name = pv_name_parser(exc2['name'])
                        # skip non pv energy producing datasets 
                        if not any('kWp' in s for s in parsed_name) : 
                            continue
                        # Clear the kWp unit from the name (it is already implied in the column name
                        parsed_name = [sub.replace('kWp','') for sub in parsed_name]                            
                        market_group_ds_storage.append((market_group[0],market_group[1],group_ds['location'],(production_sector['code'],exc2.input['code']),*parsed_name))

    # Convert to pd dataframe 
    cols_group = ['Market Dataset','ecoinvent location','Market group location','Underlying PV tech code','Installation','Peak power (kWp)','Technology','Placement','Build','Placement2']
    cols_ds = ['Market Dataset','ecoinvent location','Market group location','Underlying PV tech code','Peak power (kWp)','Installation','Technology','Placement','Build','Placement2']
    
    df1 = pd.DataFrame(market_ds_storage,columns = cols_ds)
    df2 = pd.DataFrame(market_group_ds_storage,columns = cols_group) 
    df3 = pd.concat([df1,df2],ignore_index = True)
    df3['Peak power (kWp)'] = df3['Peak power (kWp)'].astype(int)
    return df3


def pv_name_parser(ds_name): 
    """
    Extract technical information from the dataset names
    Clean up the string if there are empty fields
    """
    strings = ds_name.replace('electricity production,','')
    strings = strings.replace('photovoltaic','')
    strings = strings.replace('installation','')
    strings = strings.replace('kWp','kWp,')
    strings = str(strings).split(',')
    # Some of the elements might have returned empty or a space, lets clear that
    strings = list(filter(None, strings))
    strings = [i for i in strings if i !=" "]
    strings = [i for i in strings if "renewable" not in i]
    return strings

the_db = 'ecoinvent 3.9.1 cutoff'
the_other_db = 'SSP2-RCP19-2050'
the_other_db2 = 'image-SSP2-RCP19-2020'
validation_db = 'image-SSP2-RCP19-2025'
pv_datasets = pv_market_mixes_identifier(validation_db)    
display(pv_datasets)

Market Dataset ecoinvent location  \
0      market for electricity, low voltage, renewable...                 CH   
1      market for electricity, low voltage, renewable...                 CH   
2                    market for electricity, low voltage                 CM   
3                    market for electricity, low voltage                 CM   
4                    market for electricity, low voltage                 CM   
...                                                  ...                ...   
14118                market for electricity, low voltage                 CW   
14119                market for electricity, low voltage                 CW   
14120                market for electricity, low voltage                 CW   
14121                market for electricity, low voltage                 CW   
14122                market for electricity, low voltage                 CW   

      Market group location  \
0                       NaN   
1                       NaN   
2                       WAF   
3                       WAF   
4                       WAF   
...                     ...   
14118                  RCAM   
14119                  RCAM   
14120                  RCAM   
14121                  RCAM   
14122                  RCAM   

                                 Underlying PV tech code  Peak power (kWp)  \
0                       b0b8dacb783da5158538cac3bbf1ce88                 3   
1                       b5dae48681351a2f70efde3e7d2be6dd                 3   
2      (e5731a56e84941f08b24701b420bbc7d, 61b8feb79a0...                 3   
3      (e5731a56e84941f08b24701b420bbc7d, 0914aaaa037...                 3   
4      (e5731a56e84941f08b24701b420bbc7d, 5eeac3075af...                 3   
...                                                  ...               ...   
14118  (e5731a56e84941f08b24701b420bbc7d, c8234c88a5e...                 3   
14119  (e5731a56e84941f08b24701b420bbc7d, be605eaacd9...                 3   
14120  (e5731a56e84941f08b24701b420bbc7d, 0f97cf00e49...                 3   
14121  (e5731a56e84941f08b24701b420bbc7d, bc96527e31b...                 3   
14122  (e5731a56e84941f08b24701b420bbc7d, f63648bbd67...                 3   

         Installation  Technology   Placement        Build Placement2  
0       slanted-roof    single-Si       panel      mounted    on roof  
1       slanted-roof     multi-Si       panel      mounted    on roof  
2       slanted-roof          CIS   laminated   integrated    on roof  
3       slanted-roof         CdTe       panel      mounted    on roof  
4       slanted-roof     micro-Si   laminated   integrated    on roof  
...               ...         ...         ...          ...        ...  
14118   slanted-roof         CdTe   laminated   integrated    on roof  
14119   slanted-roof     multi-Si   laminated   integrated    on roof  
14120   slanted-roof     multi-Si       panel      mounted    on roof  
14121   slanted-roof    single-Si   laminated   integrated    on roof  
14122   slanted-roof    single-Si       panel      mounted    on roof  

[14123 rows x 10 columns]

In [23]:
coord = pd.read_csv("Coordinate_unique.csv")

def generate_pv_prod_data(coord):
    url_api = "https://re.jrc.ec.europa.eu/api/v5_2/PVcalc?"
    mktrgn_list = ["RUS","CHN","RSAF","INDO","JAP","RSAM","WAF","UKR","INDIA","ME","WEU","NAF","KOR","EAF","STAN","CEU","RCAM","CAN","RSAS","SAF","BRA","TUR","OCE","USA","SEAS"]
    tech_list = ['crystSi', 'CIS', 'CdTe', 'Unknown']
    mounting_list = ['free', 'building']
    angle_list = ['90','0']
    optincl = '1'
    poss_list = []
    test_list = []
    url_list = []
    yrlygen_list = []
    result_list = []
    
    p0 = "&peakpower=1"
    p1 = "&pvtechchoice="
    p2 = "&mountingplace="
    p3 = "&angle="
    p4 = "&optimalinclination="
    mp = "&loss=14&outputformat=json"
    
    # Boucle pour générer chaque suite et les stocker dans la troisième liste
    for e1 in tech_list:
        for e2 in mounting_list:
            if e2 == "free":
                suite_url = p0+p1+e1+p2+e2+p4+optincl+mp
                poss_list.append((suite_url, e1+" "+e2))
            else:
                for e3 in angle_list:
                    suite_url = p0+p1+e1+p2+e2+p3+e3+mp
                    poss_list.append((suite_url,e1+" "+e2+" "+e3))
    #print(poss_list)
    for region in mktrgn_list:
        coordonnees_region = coord.loc[coord['Short name'] == region, ['Latitude', 'Longitude']]
        for x in poss_list:
            for index, row in coordonnees_region.iterrows():
                lat = "lat="+"{:.2f}".format(row['Latitude'])+"&"
                lon = "lon="+"{:.2f}".format(row['Longitude'])
                url_request = url_api + lat + lon + x[0]
                #url_list.append(url_request) 
                response_test = requests.get(url_request)
                jsondata_test = response_test.json()
                if response_test.status_code == 200:
                    #print("Success")
                    jsondata_test = response_test.json()
                    yrlygen_list.append(jsondata_test["outputs"]["totals"]["fixed"]["E_y"])
            mean_E_y = np.mean(yrlygen_list)
            yrlygen_list = []
            result_list.append((region, x[1], mean_E_y))
            #print(region,x[1],mean_E_y)
    return result_list

def add_custom_production_data_to_df(pv_pickle, result_list):
    for index, row in pv_pickle.iterrows():
        for r in result_list:
            if row['Market group location'] == r[0]:
                tech_temp = row['Technology']
                mount_temp = row['Installation']
                pvtechchoice = (" crystSi" if "Si" in tech_temp
                        else " CIS" if tech_temp == " CIS"
                        else " CdTe" if tech_temp == " CdTe"
                        else " Unknown")
                mountingplace = (" building" if "roof" in mount_temp
                        else " building" if "facade" in mount_temp
                        else " free")
                angle = (" 0" if "roof" in mount_temp
                        else " 90" if "facade" in mount_temp
                        else "")
                ds_temp = str(row['Market group location'])+pvtechchoice+mountingplace+angle
                if ds_temp == str(r[0])+" "+str(r[1]):
                    pv_pickle.at[index, 'Annual production'] = r[2]
    return pv_pickle



pv_updated_ds = add_custom_production_data_to_df(pv_datasets, generate_pv_prod_data(coord))


/opt/tljh/user/envs/wurst/lib/python3.11/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/tmp/ipykernel_4065107/2003481998.py:72: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '1664.09' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  pv_pickle.at[index, 'Annual production'] = r[2]


In [24]:
display(pv_updated_ds)

Market Dataset ecoinvent location  \
0      market for electricity, low voltage, renewable...                 CH   
1      market for electricity, low voltage, renewable...                 CH   
2                    market for electricity, low voltage                 CM   
3                    market for electricity, low voltage                 CM   
4                    market for electricity, low voltage                 CM   
...                                                  ...                ...   
14118                market for electricity, low voltage                 CW   
14119                market for electricity, low voltage                 CW   
14120                market for electricity, low voltage                 CW   
14121                market for electricity, low voltage                 CW   
14122                market for electricity, low voltage                 CW   

      Market group location  \
0                       NaN   
1                       NaN   
2                       WAF   
3                       WAF   
4                       WAF   
...                     ...   
14118                  RCAM   
14119                  RCAM   
14120                  RCAM   
14121                  RCAM   
14122                  RCAM   

                                 Underlying PV tech code  Peak power (kWp)  \
0                       b0b8dacb783da5158538cac3bbf1ce88                 3   
1                       b5dae48681351a2f70efde3e7d2be6dd                 3   
2      (e5731a56e84941f08b24701b420bbc7d, 61b8feb79a0...                 3   
3      (e5731a56e84941f08b24701b420bbc7d, 0914aaaa037...                 3   
4      (e5731a56e84941f08b24701b420bbc7d, 5eeac3075af...                 3   
...                                                  ...               ...   
14118  (e5731a56e84941f08b24701b420bbc7d, c8234c88a5e...                 3   
14119  (e5731a56e84941f08b24701b420bbc7d, be605eaacd9...                 3   
14120  (e5731a56e84941f08b24701b420bbc7d, 0f97cf00e49...                 3   
14121  (e5731a56e84941f08b24701b420bbc7d, bc96527e31b...                 3   
14122  (e5731a56e84941f08b24701b420bbc7d, f63648bbd67...                 3   

         Installation  Technology   Placement        Build Placement2  \
0       slanted-roof    single-Si       panel      mounted    on roof   
1       slanted-roof     multi-Si       panel      mounted    on roof   
2       slanted-roof          CIS   laminated   integrated    on roof   
3       slanted-roof         CdTe       panel      mounted    on roof   
4       slanted-roof     micro-Si   laminated   integrated    on roof   
...               ...         ...         ...          ...        ...   
14118   slanted-roof         CdTe   laminated   integrated    on roof   
14119   slanted-roof     multi-Si   laminated   integrated    on roof   
14120   slanted-roof     multi-Si       panel      mounted    on roof   
14121   slanted-roof    single-Si   laminated   integrated    on roof   
14122   slanted-roof    single-Si       panel      mounted    on roof   

       Annual production  
0                1400.00  
1                1400.00  
2                1664.09  
3                1795.22  
4                1640.68  
...                  ...  
14118            1514.52  
14119            1426.29  
14120            1426.29  
14121            1426.29  
14122            1426.29  

[14123 rows x 11 columns]

In [36]:
#pv_datasets['Annual production'] = 1400
#display(pv_datasets)

# def retrieve_new_pv_production(pv_datasets):
#    """See with Edgar and Terry"""
#    pd.DataFrame(expected_market_pv_productions)
#    return expected_market_pv_productions

def update_pv_efficiencies(database_name,pv_datasets) : 

    """
    ADD description here
    Find a way to indicate WHICH database is assessed (remove references to "the_other_db2")
    """
    pv_db = pv_datasets.copy()

    lifetime_kwh = []
    new_lifetime_kwh = []
    Ratio = []

    # Mapping tables for premise databases 
    market_group_mapping_com = pd.read_excel('pv_com_res_shares.xlsx',sheet_name = 1,index_col = 0)
    market_group_mapping_res = pd.read_excel('pv_com_res_shares.xlsx',sheet_name = 0,index_col = 0)

    
    for row in pv_db.iterrows() : 
        code = row[1]['Underlying PV tech code']
        new_prod = row[1]['Annual production']*row[1]['Peak power (kWp)']*30
        new_lifetime_kwh.append(new_prod)

        
        if type(code) == tuple :

            ds = bd.get_activity((database_name,code[0]))
            location = ds['location']
            # Select residential or commercial : 
            tech_ds = bd.get_activity((database_name, code[1]))
            
            common_naming = [str(i) for i in row[1][4:-1] if i != None] 
            common_name = common_naming[0]+' kWp'+common_naming[1]+ 'installation,'
            common_name = common_name+','.join(common_naming[2:])
            
            if 'commercial' in ds['name'] : 
                #map_value.append(market_group_mapping_com.loc[location,common_name])
                map_val = market_group_mapping_com.loc[location,common_name]
            
            if 'residential' in ds['name']:
                #map_value.append(market_group_mapping_res.loc[location,common_name])
                map_val = market_group_mapping_res.loc[location,common_name]
            
            # Script to find the exchange amount
            for exc in ds.exchanges():                
                if exc.input['code'] == tech_ds['code'] :
                    if exc['amount'] == 0 : 
                        lifetime_kwh.append(0)
                        Ratio.append(0)
                        
                        #print('I have a 0 here!')
                    else :   
                        old_prod = map_val/exc['amount']
                        lifetime_kwh.append(old_prod)      
                        Ratio.append(old_prod/new_prod)
                        #potential_exc_amnt = exc['amount']*old_prod/new_prod 
                    
                        exc['amount'] = exc['amount']*old_prod/new_prod 
                        
                        #exc.save()
                        if np.isnan(exc['amount']) is True: 
                            print('Check for nan exchanges..')
                        

                    
                  
        else :
            code = row[1]['Underlying PV tech code']
            ds = bd.get_activity((database_name,code))

            for exc in ds.exchanges():
                if exc['type'] == 'production' : 
                    output = exc['amount'] 

                if ('photovoltaic' in exc['name']) & (exc['unit']=='unit') & ('kWp' in exc['name']) :
                    exc_amnt = exc['amount']
                    old_prod = output/exc_amnt

                    lifetime_kwh.append(old_prod)
                    Ratio.append(old_prod/new_prod)

                    exc['amount'] = exc['amount']*old_prod/new_prod 
                    if np.isnan(exc['amount']) is True: 
                        print('Check for nan exchanges')
                        
                    #exc.save()
    
    pv_db['previous production'] = lifetime_kwh  
    pv_db['new production'] = new_lifetime_kwh
    pv_db['Exchange Variation'] = Ratio
    return pv_db

pv_datasets1 = update_pv_efficiencies(validation_db,pv_updated_ds)
display(pv_datasets1)

Market Dataset ecoinvent location  \
0      market for electricity, low voltage, renewable...                 CH   
1      market for electricity, low voltage, renewable...                 CH   
2                    market for electricity, low voltage                 CM   
3                    market for electricity, low voltage                 CM   
4                    market for electricity, low voltage                 CM   
...                                                  ...                ...   
14118                market for electricity, low voltage                 CW   
14119                market for electricity, low voltage                 CW   
14120                market for electricity, low voltage                 CW   
14121                market for electricity, low voltage                 CW   
14122                market for electricity, low voltage                 CW   

      Market group location  \
0                       NaN   
1                       NaN   
2                       WAF   
3                       WAF   
4                       WAF   
...                     ...   
14118                  RCAM   
14119                  RCAM   
14120                  RCAM   
14121                  RCAM   
14122                  RCAM   

                                 Underlying PV tech code  Peak power (kWp)  \
0                       b0b8dacb783da5158538cac3bbf1ce88                 3   
1                       b5dae48681351a2f70efde3e7d2be6dd                 3   
2      (e5731a56e84941f08b24701b420bbc7d, 61b8feb79a0...                 3   
3      (e5731a56e84941f08b24701b420bbc7d, 0914aaaa037...                 3   
4      (e5731a56e84941f08b24701b420bbc7d, 5eeac3075af...                 3   
...                                                  ...               ...   
14118  (e5731a56e84941f08b24701b420bbc7d, c8234c88a5e...                 3   
14119  (e5731a56e84941f08b24701b420bbc7d, be605eaacd9...                 3   
14120  (e5731a56e84941f08b24701b420bbc7d, 0f97cf00e49...                 3   
14121  (e5731a56e84941f08b24701b420bbc7d, bc96527e31b...                 3   
14122  (e5731a56e84941f08b24701b420bbc7d, f63648bbd67...                 3   

         Installation  Technology   Placement        Build Placement2  \
0       slanted-roof    single-Si       panel      mounted    on roof   
1       slanted-roof     multi-Si       panel      mounted    on roof   
2       slanted-roof          CIS   laminated   integrated    on roof   
3       slanted-roof         CdTe       panel      mounted    on roof   
4       slanted-roof     micro-Si   laminated   integrated    on roof   
...               ...         ...         ...          ...        ...   
14118   slanted-roof         CdTe   laminated   integrated    on roof   
14119   slanted-roof     multi-Si   laminated   integrated    on roof   
14120   slanted-roof     multi-Si       panel      mounted    on roof   
14121   slanted-roof    single-Si   laminated   integrated    on roof   
14122   slanted-roof    single-Si       panel      mounted    on roof   

       Annual production  previous production  new production  \
0                1400.00             126000.0        126000.0   
1                1400.00             126000.0        126000.0   
2                1664.09                  NaN        149768.1   
3                1795.22                  NaN        161569.8   
4                1640.68                  NaN        147661.2   
...                  ...                  ...             ...   
14118            1514.52                  NaN        136306.8   
14119            1426.29                  NaN        128366.1   
14120            1426.29                  NaN        128366.1   
14121            1426.29                  NaN        128366.1   
14122            1426.29                  NaN        128366.1   

       Exchange Variation  
0                     1.0  
1                     1.0  
2                     NaN  
3            

In [37]:
 db = bd.Database(validation_db)

 for ds in db:
     for e in ds.exchanges():
         if not isinstance(e["amount"], float):
             print(e)
         try:
             int(e["amount"])
         except:
             print(e)

Exchange: nan unit 'photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof' (unit, CH, None) to 'electricity production, photovoltaic, commercial' (kilowatt hour, CH, None)>
Exchange: nan unit 'photovoltaic flat-roof installation, 156 kWp, single-Si, on roof' (unit, CH, None) to 'electricity production, photovoltaic, commercial' (kilowatt hour, CH, None)>
Exchange: nan unit 'photovoltaic open ground installation, 570 kWp, CIS, on open ground' (unit, RER, None) to 'electricity production, photovoltaic, commercial' (kilowatt hour, CH, None)>
Exchange: nan unit 'photovoltaic open ground installation, 570 kWp, CdTe, on open ground' (unit, RER, None) to 'electricity production, photovoltaic, commercial' (kilowatt hour, CH, None)>
Exchange: nan unit 'photovoltaic open ground installation, 570 kWp, micro-Si, on open ground' (unit, RER, None) to 'electricity production, photovoltaic, commercial' (kilowatt hour, CH, None)>
Exchange: nan unit 'photovoltaic open ground installation, 570 

In [28]:
import xarray as xr
# let's store this as a dict
# Creating the dictionary from the provided data

DAC_inputs = {
    "Electricity": {
        2020: 0.345,
        2025: 0.319,
        2030: 0.311,
        2035: 0.307,
        2040: 0.304,
        2045: 0.301,
        2050: 0.299
    },
    "Heat": {
        2020: 6.28,
        2025: 5.81,
        2030: 5.67,
        2035: 5.58,
        2040: 5.53,
        2045: 5.48,
        2050: 5.44
    },

}


# Convert dictionaries into an xarray Dataset
years = list(DAC_inputs['Electricity'].keys())
electricity_values = list(DAC_inputs['Electricity'].values())
heat_values = list(DAC_inputs['Heat'].values())

dataset = xr.Dataset({
    'Electricity': ('Year', electricity_values),
    'Heat': ('Year', heat_values),
}, coords={'Year': years})

def get_DAC_values_for_year(year):
    # Perform interpolation for the specified year
    interpolated_values = dataset.interp(Year=year)
    
    # Extract values for 'Electricity' and 'Heat'
    electricity = interpolated_values['Electricity'].values.item()
    heat = interpolated_values['Heat'].values.item()
    
    # Output results
    #print(f"Year: {year}")
    #print(f"Electricity: {electricity}")
    #print(f"Heat: {heat}")
    return electricity, heat
# Example usage:
get_DAC_values_for_year(2048)

(0.2998, 5.456)

In [29]:

#def find_future_DAC_efficiencies():  
#    See Praveen & Mauricio's code
#    return

year = 2025

def update_DAC_efficiencies(database_name,year,DAC_ds ='carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2' ): 
    DAC_eff_values = get_DAC_values_for_year(year)

    for ds in bd.Database(database_name) : 
        if ds['name'] == DAC_ds : 
            print(ds['name'],'----',ds['unit'])
            for exc in ds.exchanges(): 
                if 'electricity' in exc['name'] :
                    exc['amount'] = DAC_eff_values[0]
                    exc.save()
                    #print(exc['name'],'OLD --->',exc['amount'],'new ->',DAC_eff_values[0])
                    
                if 'heat' in exc['name']:
                    exc['amount'] = DAC_eff_values[1]
                    exc.save()
                    #print(exc['name'],exc['amount'],'new ->',DAC_eff_values[1])

                
                #print(exc['name'], exc['type'])

    
    return 

def generate_new_DAC_inventories(database_name,DAC_ds ='carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2'):
    """
    Create new DAC inventories based off the RER DAC dataset from premise
        - Find DAC dataset
        - Search the updated pv dataset table, for each matching electricity markets, create new DAC
        - Change the location
    """

    list_elec_mixes = []
    
    # Find the base dataset :
    for ds in bd.Database(database_name) : 
        if ds['name'] == DAC_ds : 
            base_ds = ds#ds.copy()

    # List the energy mixes available : 
    for exc in base_ds.exchanges() : 
        if 'electricity' in exc['name'] :
            elec_ds_name = exc['name']
            #print(exc['name'])

    for elec_ds in bd.Database(database_name) : 
        if elec_ds['name'] == elec_ds_name :
            print(elec_ds['name'],elec_ds['location'])
    
    #hp_qc=hp_ch.copy()
    #hp_qc['location']='CA-QC'
    # Assign the electricity input you want to change to a variable
    #elect_to_hp = [exc for exc in hp_qc.technosphere() if 'electricity, low voltage' in exc['name']][0]
    # Change the input of this exchange so it links to `qc_elect`  
    #elect_to_hp.input = qc_elect  
    # Save the resulting activity
    #elect_to_hp.save()

    return



update_DAC_efficiencies(validation_db,year)
generate_new_DAC_inventories(validation_db)



carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2 ---- kilogram
market group for electricity, medium voltage CAN
market group for electricity, medium voltage CEU
market group for electricity, medium voltage SAF
market group for electricity, medium voltage RSAF
market group for electricity, medium voltage INDO
market group for electricity, medium voltage CA
market group for electricity, medium voltage BRA
market group for electricity, medium voltage EAF
market group for electricity, medium voltage CHN
market group for electricity, medium voltage RAF
market group for electricity, medium voltage STAN
market group for electricity, medium voltage RNA
market group for electricity, medium voltage UKR
market group for electricity, medium voltage WEU
market group for electricity, medium voltage USA
market group for electricity, medium voltage SEAS
market group for electricity, medium voltage INDIA
market group for electricity, medium voltage GLO
ma

In [30]:
DAC_list = []

for ds in bd.Database(validation_db): 
    if ds['name'] == 'carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2':
        DAC_list.append((validation_db,ds['code']))
print(DAC_list)

[('image-SSP2-RCP19-2025', 'a8fa412ff04c47a4aa3d22c51d127f2c')]


In [31]:
for method in bd.methods:
#.Methods():
    print(method)
our_method = ('IPCC 2021', 'climate change: biogenic', 'global warming potential (GWP100)')

('CML v4.8 2016 no LT', 'acidification no LT', 'acidification (incl. fate, average Europe total, A&B) no LT')
('CML v4.8 2016 no LT', 'climate change no LT', 'global warming potential (GWP100) no LT')
('CML v4.8 2016 no LT', 'ecotoxicity: freshwater no LT', 'freshwater aquatic ecotoxicity (FAETP inf) no LT')
('CML v4.8 2016 no LT', 'ecotoxicity: marine no LT', 'marine aquatic ecotoxicity (MAETP inf) no LT')
('CML v4.8 2016 no LT', 'ecotoxicity: terrestrial no LT', 'terrestrial ecotoxicity (TETP inf) no LT')
('CML v4.8 2016 no LT', 'energy resources: non-renewable no LT', 'abiotic depletion potential (ADP): fossil fuels no LT')
('CML v4.8 2016 no LT', 'eutrophication no LT', 'eutrophication (fate not incl.) no LT')
('CML v4.8 2016 no LT', 'human toxicity no LT', 'human toxicity (HTP inf) no LT')
('CML v4.8 2016 no LT', 'material resources: metals/minerals no LT', 'abiotic depletion potential (ADP): elements (ultimate reserves) no LT')
('CML v4.8 2016 no LT', 'ozone depletion no LT', 'oz

In [32]:
print(validation_db)

image-SSP2-RCP19-2025


In [33]:
print(DAC_list[0])

('image-SSP2-RCP19-2025', 'a8fa412ff04c47a4aa3d22c51d127f2c')


In [34]:
lca = bc.LCA(demand={DAC_list[0]: 1}, method=our_method)#, use_distributions=True,seed_override=343)
lca.lci()
lca.lcia()

ValueError: Invalid amount in exchange {'name': 'photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof', 'amount': nan, 'location': 'CH', 'unit': 'unit', 'type': 'technosphere', 'uncertainty type': 0, 'reference product': 'photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof', 'comment': '(2,2,1,1,1,3); Calculation with average annual yield and share of technologies. Lifetime: 30a.', 'product': 'photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof', 'loc': 7.150753987150537e-08, 'scale': nan, 'shape': nan, 'minimum': nan, 'maximum': nan, 'input': ('image-SSP2-RCP19-2025', '90e8cd12bbf34ec1a583373dfbd06732'), 'output': ('image-SSP2-RCP19-2025', 'b1aeaf37d0bd4027abc939b89d39e693')}

In [ ]:
lca.score

In [19]:
#del bd.databases['SSP2-RCP19-2050']



In [20]:
tes = bd.get_activity(('SSP2-RCP19-2050', '0431b91184d64c2691e582402a2d8922'))

In [39]:
for exc in tes.exchanges():
    #print(exc['amount'])
    if ('570 kWp' in exc['name']) :
        print(exc['name'],exc['amount'])
        if np.isnan(exc['amount']) == True: 
            print('')

photovoltaic open ground installation, 570 kWp, CIS, on open ground 2.4551823445489174e-10
photovoltaic open ground installation, 570 kWp, CdTe, on open ground 9.461671090652942e-09
photovoltaic open ground installation, 570 kWp, micro-Si, on open ground nan

photovoltaic open ground installation, 570 kWp, multi-Si, on open ground 1.261556145420392e-08
photovoltaic open ground installation, 570 kWp, single-Si, on open ground 6.695951848769774e-09


In [47]:
ds_interest = []
for ds in bd.Database(the_other_db) : 
    if 'market group for electricity, medium voltage' in ds['name'] : 
        ds_interest.append((the_other_db,ds['code']))
        
        #print(ds['name'],ds['location'])                     

In [49]:
a_ds = bd.get_activity(ds_interest[5])

print(a_ds['name'],a_ds['location'])

for exc in a_ds.exchanges() : 
    print(exc['name'])



market group for electricity, medium voltage, 20-year period BRA
market group for electricity, medium voltage, 20-year period
market group for electricity, high voltage, 20-year period
market group for electricity, medium voltage, 20-year period
market for sulfur hexafluoride, liquid
Sulfur hexafluoride
transmission network construction, electricity, medium voltage


In [43]:
print(ds_interest[0])

('SSP2-RCP19-2050', 'c7bb74394f3ba9dbcfedf48afaba9b3c')


In [129]:
selected_cols = ['Market group location','Peak power (kWp)','Installation','Technology']

pv_datasets['combined_data'] = pv_datasets['Market group location'] + pv_datasets['Peak power (kWp)'].astype(str)+pv_datasets['Installation']+pv_datasets['Technology']
print(len(pv_datasets['combined_data'].unique()))

pv_datasets['combined_data2'] = pv_datasets['Market group location']+pv_datasets['Installation']+pv_datasets['Technology']
print(len(pv_datasets['combined_data2'].unique()))

pv_datasets['combined_data3'] = pv_datasets['Installation']+pv_datasets['Technology']
print(len(pv_datasets['combined_data3'].unique()))

print(26*14)

469
365
14
364


### Figure out the amount of square meters and expected lifespan of the panels

In [154]:
for ds in bd.Database(the_db) :
    if ('photovoltaic' in ds['name']) & (ds['unit']=='unit') & ('market' not in ds['name']): 
        #print(ds['name'])
        try : 
            year = int(ds['comment'].split(' years')[0][-2:])
            print(ds['name'],year)
        except : 
            print(f"--->{ds['name']} has no numerical year.")
    
   # pass

photovoltaic flat-roof installation, 3kWp, multi-Si, on roof 30
photovoltaic slanted-roof installation, 3kWp, multi-Si, panel, mounted, on roof 30
photovoltaic slanted-roof installation, 3kWp, single-Si, panel, mounted, on roof 30
photovoltaic flat-roof installation, 3kWp, single-Si, on roof 30
--->photovoltaics, electric installation for 3kWp module, at building has no numerical year.
photovoltaic slanted-roof installation, 3kWp, CdTe, laminated, integrated, on roof 30
photovoltaic slanted-roof installation, 3kWp, multi-Si, laminated, integrated, on roof 30
photovoltaic facade installation, 3kWp, single-Si, laminated, integrated, at building 30
photovoltaic slanted-roof installation, 3kWp, multi-Si, laminated, integrated, on roof 30
photovoltaic slanted-roof installation, 3kWp, a-Si, panel, mounted, on roof 30
photovoltaic slanted-roof installation, 3kWp, a-Si, laminated, integrated, on roof 30
photovoltaic slanted-roof installation, 3kWp, CIS, panel, mounted, on roof 30
photovoltaic 

In [201]:
for row in pv_datasets.iterrows() : 
    ds = bd.get_activity((the_other_db2,row[1]['Underlying PV tech code']))
    
    
    print(ds['name'],ds['location'],ds['reference product'])

electricity production, photovoltaic, 3kWp slanted-roof installation, single-Si, panel, mounted, renewable energy produc CH electricity, low voltage, renewable energy products
electricity production, photovoltaic, 3kWp slanted-roof installation, multi-Si, panel, mounted, renewable energy product CH electricity, low voltage, renewable energy products
photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof CH photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof
photovoltaic flat-roof installation, 156 kWp, single-Si, on roof CH photovoltaic flat-roof installation, 156 kWp, single-Si, on roof
photovoltaic open ground installation, 570 kWp, CIS, on open ground RER photovoltaic open ground installation, 570 kWp, CIS, on open ground
photovoltaic open ground installation, 570 kWp, CdTe, on open ground RER photovoltaic open ground installation, 570 kWp, CdTe, on open ground
photovoltaic open ground installation, 570 kWp, micro-Si, on open ground RER photovoltaic open ground 

In [200]:
for row in pv_datasets.iterrows() : 
    ds = bd.get_activity((the_other_db2,row[1]['Underlying PV tech code']))
    print('--->',ds['name'])
    for exc in ds.exchanges() : 
        if ('photovoltaic' in exc['name']) & (exc['unit']=='unit') & ('kWp' in exc['name']) :#& ('electric inst' not in exc['name']): 
           # print(exc['type'])
            #pv_unit_ds = bd.get_activity((the_other_db2,exc.input['code']))
            print(exc['amount'],exc['unit'],exc['type'],exc['name'])
            #if 'market' in exc['name'] :
            #    print('oops - market!')


            

            #print(exc.input.as_dict().keys())#['amount'])
            #for exc2 in pv_unit_ds.exchanges(): 
            #    #print(exc2['name'])
            #    if (exc2['unit'] =='square meter') & ('mounting' not in exc2['name']) & (exc2['type'] != 'production') & ('panel' in exc2['name']):
            #        print(exc2['name'],exc2.amount)
                                    


---> electricity production, photovoltaic, 3kWp slanted-roof installation, single-Si, panel, mounted, renewable energy produc
1.2051e-05 unit technosphere photovoltaic slanted-roof installation, 3kWp, single-Si, panel, mounted, on roof
---> electricity production, photovoltaic, 3kWp slanted-roof installation, multi-Si, panel, mounted, renewable energy product
1.2051e-05 unit technosphere photovoltaic slanted-roof installation, 3kWp, multi-Si, panel, mounted, on roof
---> photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof
1.0 unit production photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof
1.0 unit technosphere electric installation, 156 kWp photovoltaic plant, at plant
---> photovoltaic flat-roof installation, 156 kWp, single-Si, on roof
1.0 unit production photovoltaic flat-roof installation, 156 kWp, single-Si, on roof
1.0 unit technosphere electric installation, 156 kWp photovoltaic plant, at plant
---> photovoltaic open ground installation, 570 kWp, CIS,

In [210]:
DAC_ds = 'carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2'


In [215]:
for ds in bd.Database(the_other_db2) : 
    if ds['name'] == DAC_ds : 
        print(ds['name'],'----',ds['unit'])
        for exc in ds.exchanges(): 
            print(exc['name'], exc['type'])

carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2 ---- kilogram
carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2 production
direct air capture system, solvent-based, 1MtCO2 technosphere
treatment of direct air capture system, solvent-based, 1MtCO2 technosphere
market for tap water technosphere
market for potassium hydroxide technosphere
market for limestone, crushed, for mill technosphere
Carbon dioxide, in air biosphere
Carbon dioxide, non-fossil biosphere
market group for electricity, medium voltage technosphere
heat production, natural gas, at industrial furnace >100kW technosphere


In [104]:
import pickle
with open(fr"pv_details{the_other_db}.pickle", "wb") as output_file:
    pickle.dump(pv_datasets, output_file)

In [214]:
# storage = []

# for ds in bd.Database('SSP2-RCP19-2050') : 
#     if 'market for electricity' in ds['name']: 

#         for exc1 in ds.exchanges() : 
# #            print(exc1)
#             if 'market group for electricity' in exc1['name']:
#                 #print(exc1['name'])
#                 for exc2 in bd.get_activity(exc1['input']).exchanges():
#                 #print(bd.get_activity(exc1['input']))
#                 #for exc2 in exc1.exchanges(): 
#                     if 'photovoltaic' in exc2['name']:
#                         #print(exc2['name'],bd.get_activity(exc2['input'])['name'])
                        
#                         for exc3 in bd.get_activity(exc2['input']).exchanges(): 
#                             #print(exc3['name'])
#                             if 'photovoltaic' in exc3['name'] : 
#                                 strings = str(exc3['name']).split(',')
#                                 #print(strings)

#                                 # Clear non production datasets
#                                 if not any('kWp' in s for s in strings) : 
#                                     #print('here')
#                                     continue

#                                 # Edit the strings :
#                                 if 'MWp' in strings[1] : 
#                                     strings[1] = 1000*int(strings[1].replace('MWp',''))
#                                 if 'kWp' in strings[1] : 
#                                     strings[1] = int(strings[1].replace('kWp',''))
#                                 if 'installation' in strings[0] : 
#                                     strings[0] = strings[0].replace('installation','')
#                                 if 'photovoltaic' in strings[0] : 
#                                     strings[0] = strings[0].replace('photovoltaic','')

#                                 storage.append((ds['name'],ds['location'],exc1['location'],*strings))

            
# import pandas as pd
# df = pd.DataFrame(storage)
# df.columns= ['Market Dataset','ecoinvent location','Market group location','Installation','Peak power','Technology','Placement','Build','Placement2']
# display(df)

# import pickle
# with open(r"pv_details.pickle", "wb") as output_file:
#     pickle.dump(df, output_file)

Market Dataset ecoinvent location  \
0      market for electricity, high voltage             US-MRO   
1      market for electricity, high voltage             US-MRO   
2      market for electricity, high voltage             US-MRO   
3      market for electricity, high voltage             US-MRO   
4      market for electricity, high voltage             US-MRO   
...                                     ...                ...   
14116  market for electricity, high voltage             CN-NWG   
14117  market for electricity, high voltage             CN-NWG   
14118  market for electricity, high voltage             CN-NWG   
14119  market for electricity, high voltage             CN-NWG   
14120  market for electricity, high voltage             CN-NWG   

      Market group location    Installation  Peak power  Technology  \
0                       USA      flat-roof          156    multi-Si   
1                       USA      flat-roof          156   single-Si   
2                       USA    open ground          570         CIS   
3                       USA    open ground          570        CdTe   
4                       USA    open ground          570    micro-Si   
...                     ...             ...         ...         ...   
14116                   CHN    open ground          570   single-Si   
14117                   CHN   slanted-roof           93    multi-Si   
14118                   CHN   slanted-roof           93    multi-Si   
14119                   CHN   slanted-roof           93   single-Si   
14120                   CHN   slanted-roof           93   single-Si   

             Placement        Build Placement2  
0              on roof         None       None  
1              on roof         None       None  
2       on open ground         None       None  
3       on open ground         None       None  
4       on open ground         None       None  
...                ...          ...        ...  
14116   on open ground         None       None  
14117        laminated   integrated    on roof  
14118            panel      mounted    on roof  
14119        laminated   integrated    on roof  
14120            panel      mounted    on roof  

[14121 rows x 9 columns]